In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.metrics import accuracy_score, precision_recall_fscore_support, confusion_matrix
from sklearn.manifold import TSNE
import umap
import time
from scipy.spatial.distance import pdist, squareform
from scipy.stats import pearsonr
import math

In [11]:
%reload_ext kedro.ipython

[05/28/25 20:29:46] INFO     Registered line magic '%reload_kedro'                                   ]8;id=961266;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/ipython/__init__.py\__init__.py]8;;\:]8;id=750463;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/ipython/__init__.py#63\63]8;;\

                    INFO     Registered line magic '%load_node'                                      ]8;id=934701;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/ipython/__init__.py\__init__.py]8;;\:]8;id=558476;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/ipython/__init__.py#65\65]8;;\

                    INFO     Resolved project path as:                                              ]8;id=672872;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/ipython/__init__.py\__init__.py]8;;\:]8;id=732385;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/ipython/__init__.py#180\180]8;;\
                             /Users/RoverHofman/Desktop/School/thesis/embedding-forecasting.                       
                             To set a different path, run '%reload_kedro <project_root>'                           

[05/28/25 20:29:47] WARNING  /Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/l ]8;id=212313;file:///Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/warnings.py\warnings.py]8;;\:]8;id=413301;file:///Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/warnings.py#109\109]8;;\
                             ib/python3.11/site-packages/kedro/io/data_catalog.py:165:                             
                             KedroDeprecationWarning: `DataCatalog` has been deprecated and will be                
                             replaced by `KedroDataCatalog`, in Kedro 1.0.0.Currently some                         
                             `KedroDataCatalog` APIs have been retained for compatibility with                     
                             `DataCatalog`, including the `datasets` property and the                              
                             `get_datasets`, `_get_datasets`, `add`,` list`, `add_feed_dict`, and                  
                             `shallow_copy` methods. These will be removed or replaced with updated                
                             alternatives in Kedro 1.0.0. For more details, refer to the                           
                             documentation:                                                                        
                             https://docs.kedro.org/en/stable/data/index.html#kedrodatacatalog-expe                
                             rimental-feature                                                                      
                               warnings.warn(                                                                      
                                                                                                                   

[05/28/25 20:29:48] WARNING  /Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/l ]8;id=231079;file:///Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/warnings.py\warnings.py]8;;\:]8;id=685101;file:///Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/warnings.py#109\109]8;;\
                             ib/python3.11/site-packages/kedro/io/core.py:355:                                     
                             KedroDeprecationWarning: The MatplotlibWriter class has been renamed                  
                             to MatplotlibDataset. The MatplotlibWriter name is deprecated and will                
                             be removed in a future release.                                                       
                               init_func(self, *args, **kwargs)                                                    
                                                                                                                   

...

                    INFO     Creating ResNet50 embedding pipeline                                     ]8;id=822915;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/src/embedding_forecasting/pipelines/resnet_embedding/pipeline.py\pipeline.py]8;;\:]8;id=502474;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/src/embedding_forecasting/pipelines/resnet_embedding/pipeline.py#6\6]8;;\

[05/28/25 20:29:53] INFO     Kedro is sending anonymous usage data with the sole purpose of improving ]8;id=638625;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro_telemetry/plugin.py\plugin.py]8;;\:]8;id=470734;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro_telemetry/plugin.py#233\233]8;;\
                             the product. No personal data or IP addresses are stored on our side. If              
                             you want to opt out, set the `KEDRO_DISABLE_TELEMETRY` or `DO_NOT_TRACK`              
                             environment variables, or create a `.telemetry` file in the current                   
                             working directory with the contents `consent: false`. Read more at                    
                             https://docs.kedro.org/en/stable/configuration/telemetry.html                         

                    INFO     Kedro project embedding_forecasting                                    ]8;id=656994;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/ipython/__init__.py\__init__.py]8;;\:]8;id=281710;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/ipython/__init__.py#146\146]8;;\

                    INFO     Defined global variable 'context', 'session', 'catalog' and            ]8;id=46477;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/ipython/__init__.py\__init__.py]8;;\:]8;id=998435;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/ipython/__init__.py#147\147]8;;\
                             'pipelines'                                                                           

                    INFO     Registered line magic 'run_viz'                                        ]8;id=684485;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/ipython/__init__.py\__init__.py]8;;\:]8;id=89473;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/ipython/__init__.py#153\153]8;;\

In [2]:
all_datasets = catalog.list()
train_datasets = [name for name in all_datasets if name.endswith("_train")]
print(all_datasets)

['closing_prices', 'train_prices', 'val_prices', 'test_prices', 'windows_90_train', 'windows_90_val', 'windows_90_test', 'autoencoder_train', 'autoencoder_val', 'autoencoder_test', 'autoencoder_plots', 'pca_train', 'pca_val', 'pca_test', 'lle_train', 'lle_val', 'lle_test', 'umap_train', 'umap_val', 'umap_test', 'wavelet_train', 'wavelet_val', 'wavelet_test', 'fft_train', 'fft_val', 'fft_test', 'graph_train', 'graph_val', 'graph_test', 'tda_train', 'tda_val', 'tda_test', 'gaf_train', 'gaf_val', 'gaf_test', 'mtf_train', 'mtf_val', 'mtf_test', 'rp_train', 'rp_val', 'rp_test', 'gaf_clip_train', 'gaf_clip_val', 'gaf_clip_test', 'mtf_clip_train', 'mtf_clip_val', 'mtf_clip_test', 'rp_clip_train', 'rp_clip_val', 'rp_clip_test', 'gaf_dino_train', 'gaf_dino_val', 'gaf_dino_test', 'mtf_dino_train', 'mtf_dino_val', 'mtf_dino_test', 'rp_dino_train', 'rp_dino_val', 'rp_dino_test', 'gaf_resnet_train', 'gaf_resnet_val', 'gaf_resnet_test', 'mtf_resnet_train', 'mtf_resnet_val', 'mtf_resnet_test', 'rp_re

In [3]:
import numpy as np
import pandas as pd
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score, classification_report

def label_windows(series, window_size, threshold=0.01):
    """
    Labels each rolling window of length `window_size` in a 1D numeric array.
    Expects `series` to be a 1D array of floats.
    """
    arr = np.asarray(series, dtype=float)
    rets = (arr[window_size-1:] - arr[:-window_size+1]) / arr[:-window_size+1]
    labels = np.where(rets > threshold, 2,
             np.where(rets < -threshold, 0, 1))
    return labels.astype(int)


# 1) Load raw price‐DataFrames
train_df = catalog.load("train_prices")
val_df   = catalog.load("val_prices")
test_df  = catalog.load("test_prices")

# 2) Extract the numeric price series
window_size = 90
price_train = train_df["price_close"].astype(float).values
price_val   = val_df["price_close"].astype(float).values
price_test  = test_df["price_close"].astype(float).values

# 3) Compute labels
y_train = label_windows(price_train, window_size)
y_val   = label_windows(price_val,   window_size)
y_test  = label_windows(price_test,  window_size)

# 4) Discover which prefixes to evaluate (skip pure-image ones)
skip_images = {"gaf", "mtf", "rp"}
all_datasets   = catalog.list()
train_datasets = [n for n in all_datasets if n.endswith("_train")]
all_prefixes   = {ds.rsplit("_",1)[0] for ds in train_datasets}

embedding_prefixes = sorted(
    p for p in all_prefixes
    if not p.startswith(f"windows_{window_size}")
    and p not in skip_images
)

print("Will train/evaluate on:", embedding_prefixes)

# 5) Train & evaluate
for prefix in embedding_prefixes:
    print(f"\n=== {prefix} ===")
    raw_X_train = catalog.load(f"{prefix}_train")
    raw_X_test  = catalog.load(f"{prefix}_test")
    
    # coerce lists/DFs/Series into 2D np arrays
    X_train = np.asarray(raw_X_train, dtype=float)
    if X_train.ndim == 1:
        X_train = X_train.reshape(-1, 1)
    X_test  = np.asarray(raw_X_test,  dtype=float)
    if X_test.ndim  == 1:
        X_test  = X_test.reshape(-1, 1)
    
    clf = LogisticRegression(multi_class="multinomial", max_iter=1_000)
    clf.fit(X_train, y_train)
    y_pred = clf.predict(X_test)
    
    print("Accuracy:", accuracy_score(y_test, y_pred))
    print(classification_report(
        y_test, y_pred,
        target_names=["Bear","Neutral","Bull"]
    ))


[05/28/25 20:40:38] INFO     Loading data from train_prices (ParquetDataset)...                 ]8;id=792985;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=867539;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from val_prices (ParquetDataset)...                   ]8;id=815749;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=231695;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from test_prices (ParquetDataset)...                  ]8;id=224191;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=66595;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

Will train/evaluate on: ['autoencoder', 'fft', 'gaf_clip', 'gaf_dino', 'gaf_resnet', 'graph', 'lle', 'mtf_clip', 'mtf_dino', 'mtf_resnet', 'pca', 'rp_clip', 'rp_dino', 'rp_resnet', 'tda', 'umap', 'wavelet']

=== autoencoder ===


                    INFO     Loading data from autoencoder_train (ParquetDataset)...            ]8;id=657085;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=326402;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

...

Accuracy: 0.7359426681367145
              precision    recall  f1-score   support

        Bear       0.54      0.68      0.61       439
     Neutral       0.10      0.06      0.07       116
        Bull       0.86      0.82      0.84      1259

    accuracy                           0.74      1814
   macro avg       0.50      0.52      0.51      1814
weighted avg       0.74      0.74      0.73      1814


=== rp_resnet ===


                    INFO     Loading data from rp_resnet_train (PickleDataset)...               ]8;id=288687;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=527772;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from rp_resnet_test (PickleDataset)...                ]8;id=881830;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=768606;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

[05/28/25 20:44:06] WARNING  /Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/l ]8;id=777910;file:///Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/warnings.py\warnings.py]8;;\:]8;id=283963;file:///Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/warnings.py#109\109]8;;\
                             ib/python3.11/site-packages/sklearn/linear_model/_logistic.py:1247:                   
                             FutureWarning: 'multi_class' was deprecated in version 1.5 and will be                
                             removed in 1.7. From then on, it will always use 'multinomial'. Leave                 
                             it to its default value to avoid this warning.                                        
                               warnings.warn(                                                                      
                                                                                                                   

╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <module>:63                                                                                   │
│                                                                                                  │
│   60 │   │   X_test  = X_test.reshape(-1, 1)                                                     │
│   61 │                                                                                           │
│   62 │   clf = LogisticRegression(multi_class="multinomial", max_iter=1_000)                     │
│ ❱ 63 │   clf.fit(X_train, y_train)                                                               │
│   64 │   y_pred = clf.predict(X_test)                                                            │
│   65 │                                                                                           │
│   66 │   print("Accuracy:", accuracy_score(y_test, y_pred))                                      │
│                                                                                                  │
│ /Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-package │
│ s/sklearn/base.py:1389 in wrapper                                                                │
│                                                                                                  │
│   1386 │   │   │   │   │   prefer_skip_nested_validation or global_skip_validation               │
│   1387 │   │   │   │   )                                                                         │
│   1388 │   │   │   ):                                                                            │
│ ❱ 1389 │   │   │   │   return fit_method(estimator, *args, **kwargs)                             │
│   1390 │   │                                                                                     │
│   1391 │   │   return wrapper                                                                    │
│   1392                                                                                           │
│                                                                                                  │
│ /Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-package │
│ s/sklearn/linear_model/_logistic.py:1350 in fit                                                  │
│                                                                                                  │
│   1347 │   │   else:                                                                             │
│   1348 │   │   │   n_threads = 1                                                                 │
│   1349 │   │                                                                                     │
│ ❱ 1350 │   │   fold_coefs_ = Parallel(n_jobs=self.n_jobs, verbose=self.verbose, prefer=prefer)(  │
│   1351 │   │   │   path_func(                                                                    │
│   1352 │   │   │   │   X,                                                                        │
│   1353 │   │   │   │   y,                                                                        │
│                                                                                                  │
│ /Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-package │
│ s/sklearn/utils/parallel.py:77 in __call__                                                       │
│                                                                                                  │
│    74 │   │   │   (_with_config(delayed_func, config), args, kwargs)                             │
│    75 │   │   │   for delayed_func, args, kwargs in iterable                                     │
│    76 │   │   )                                                                                  │
│ ❱  77 │   │   return super().__call__(iterable_with_config)

In [4]:
import numpy as np

# correct imports
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import f1_score

def create_raw_windows(series, window_size):
    arr = np.asarray(series, dtype=float)
    return [arr[i:i+window_size] for i in range(len(arr) - window_size + 1)]

def realized_volatility(windows):
    return np.array([np.std(np.diff(np.log(w))) for w in windows])

# — PARAMETERS —
window_size = 90
skip_images = {"gaf", "mtf", "rp"}

# 1) Load train/test price series
train_df = catalog.load("train_prices")
test_df  = catalog.load("test_prices")
price_train = train_df["price_close"].astype(float).values
price_test  = test_df["price_close"].astype(float).values

# 2) Build windows & compute train thresholds
raw_wins_train = create_raw_windows(price_train, window_size)
vols_train     = realized_volatility(raw_wins_train)

thresh_25 = np.percentile(vols_train, 75)
y_binary_train = (vols_train >= thresh_25).astype(int)

low_thr, high_thr = np.percentile(vols_train, [33, 66])
y_multi_train = np.digitize(vols_train, bins=[low_thr, high_thr], right=True)

# 3) Apply thresholds on test set
raw_wins_test  = create_raw_windows(price_test, window_size)
vols_test      = realized_volatility(raw_wins_test)
y_binary_test  = (vols_test >= thresh_25).astype(int)
y_multi_test   = np.digitize(vols_test, bins=[low_thr, high_thr], right=True)

# 4) Discover embedding prefixes
all_ds   = catalog.list()
train_ds = [n for n in all_ds if n.endswith("_train")]
prefixes = sorted({
    ds.rsplit("_",1)[0] for ds in train_ds
    if not ds.startswith(f"windows_{window_size}") and ds.rsplit("_",1)[0] not in skip_images
})

# 5) Classifier pool
classifiers = {
    "LogisticRegression":   LogisticRegression(max_iter=500),
    "RandomForest":         RandomForestClassifier(n_estimators=100, random_state=42),
    "GradientBoosting":     GradientBoostingClassifier(n_estimators=100, random_state=42),
    "SVM (RBF kernel)":     SVC(kernel='rbf', probability=True, random_state=42),
    "K-Nearest Neighbors":  KNeighborsClassifier(n_neighbors=5),
}

def weighted_f1(clf, X_tr, y_tr, X_te, y_te):
    clf.fit(X_tr, y_tr)
    return f1_score(y_te, clf.predict(X_te), average="weighted")

# 6) Loop over embeddings → run both tasks
for prefix in prefixes:
    print(f"\n=== {prefix} ===")
    X_tr = np.asarray(catalog.load(f"{prefix}_train"), dtype=float)
    X_te = np.asarray(catalog.load(f"{prefix}_test"),  dtype=float)
    if X_tr.ndim == 1: X_tr = X_tr.reshape(-1,1)
    if X_te.ndim == 1: X_te = X_te.reshape(-1,1)
    
    print("  BINARY (low vs high vol):")
    for name, clf in classifiers.items():
        score = weighted_f1(clf, X_tr, y_binary_train, X_te, y_binary_test)
        print(f"    {name:25s} → wF1 = {score:.4f}")
    
    print("  MULTI-CLASS (low/med/high):")
    for name, clf in classifiers.items():
        if name == "LogisticRegression":
            clf = LogisticRegression(
                multi_class="multinomial", solver="lbfgs", max_iter=500
            )
        score = weighted_f1(clf, X_tr, y_multi_train, X_te, y_multi_test)
        print(f"    {name:25s} → wF1 = {score:.4f}")


[05/28/25 20:44:35] INFO     Loading data from train_prices (ParquetDataset)...                 ]8;id=790832;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=284373;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

[05/28/25 20:44:36] INFO     Loading data from test_prices (ParquetDataset)...                  ]8;id=407245;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=862452;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\


=== autoencoder ===


                    INFO     Loading data from autoencoder_train (ParquetDataset)...            ]8;id=896494;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=973227;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from autoencoder_test (ParquetDataset)...             ]8;id=613533;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=349883;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

...

    LogisticRegression        → wF1 = 0.4116
    RandomForest              → wF1 = 0.4493
    GradientBoosting          → wF1 = 0.4264
    SVM (RBF kernel)          → wF1 = 0.4245
    K-Nearest Neighbors       → wF1 = 0.4426

=== fft ===


[05/28/25 20:48:52] INFO     Loading data from fft_train (ParquetDataset)...                    ]8;id=239363;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=257328;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from fft_test (ParquetDataset)...                     ]8;id=264952;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=707830;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

  BINARY (low vs high vol):
    LogisticRegression        → wF1 = 0.5218
    RandomForest              → wF1 = 0.4948


╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <module>:74                                                                                   │
│                                                                                                  │
│   71 │                                                                                           │
│   72 │   print("  BINARY (low vs high vol):")                                                    │
│   73 │   for name, clf in classifiers.items():                                                   │
│ ❱ 74 │   │   score = weighted_f1(clf, X_tr, y_binary_train, X_te, y_binary_test)                 │
│   75 │   │   print(f"    {name:25s} → wF1 = {score:.4f}")                                        │
│   76 │                                                                                           │
│   77 │   print("  MULTI-CLASS (low/med/high):")                                                  │
│                                                                                                  │
│ in weighted_f1:61                                                                                │
│                                                                                                  │
│   58 }                                                                                           │
│   59                                                                                             │
│   60 def weighted_f1(clf, X_tr, y_tr, X_te, y_te):                                               │
│ ❱ 61 │   clf.fit(X_tr, y_tr)                                                                     │
│   62 │   return f1_score(y_te, clf.predict(X_te), average="weighted")                            │
│   63                                                                                             │
│   64 # 6) Loop over embeddings → run both tasks                                                  │
│                                                                                                  │
│ /Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-package │
│ s/sklearn/base.py:1389 in wrapper                                                                │
│                                                                                                  │
│   1386 │   │   │   │   │   prefer_skip_nested_validation or global_skip_validation               │
│   1387 │   │   │   │   )                                                                         │
│   1388 │   │   │   ):                                                                            │
│ ❱ 1389 │   │   │   │   return fit_method(estimator, *args, **kwargs)                             │
│   1390 │   │                                                                                     │
│   1391 │   │   return wrapper                                                                    │
│   1392                                                                                           │
│                                                                                                  │
│ /Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-package │
│ s/sklearn/ensemble/_gb.py:787 in fit                                                             │
│                                                                                                  │
│    784 │   │   │   self._resize_state()                                                          │
│    785 │   │                                                                                     │
│    786 │   │   # fit the boosting stages                                                         │
│ ❱  787 │   │   n_stages = self._fit_stages(                                                      │
│    788 │   │   │   X_train,                                

In [5]:
import numpy as np

# correct imports
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import f1_score

def create_raw_windows(series, window_size):
    arr = np.asarray(series, dtype=float)
    return [arr[i:i+window_size] for i in range(len(arr) - window_size + 1)]

def realized_volatility(windows):
    return np.array([np.std(np.diff(np.log(w))) for w in windows])

# — PARAMETERS —
window_size = 90
skip_images = {"gaf", "mtf", "rp"}

# 1) Load price series & build vol‐based labels
train_df = catalog.load("train_prices")
test_df  = catalog.load("test_prices")
price_train = train_df["price_close"].values.astype(float)
price_test  = test_df["price_close"].values.astype(float)

wins_tr = create_raw_windows(price_train, window_size)
wins_te = create_raw_windows(price_test,  window_size)
vols_tr = realized_volatility(wins_tr)
vols_te = realized_volatility(wins_te)

# binary
thresh_25       = np.percentile(vols_tr, 75)
y_binary_train  = (vols_tr >= thresh_25).astype(int)
y_binary_test   = (vols_te >=  thresh_25).astype(int)

# multi
low_thr, high_thr = np.percentile(vols_tr, [33, 66])
y_multi_train    = np.digitize(vols_tr, bins=[low_thr, high_thr], right=True)
y_multi_test     = np.digitize(vols_te, bins=[low_thr, high_thr], right=True)

# 2) Discover embeddings
all_ds   = catalog.list()
train_ds = [n for n in all_ds if n.endswith("_train")]
prefixes = sorted({
    ds.rsplit("_",1)[0] for ds in train_ds
    if not ds.startswith(f"windows_{window_size}") and ds.rsplit("_",1)[0] not in skip_images
})

# 3) Load & concatenate all embeddings into one big feature matrix
X_tr_parts = []
X_te_parts = []
for prefix in prefixes:
    arr_tr = np.asarray(catalog.load(f"{prefix}_train"), dtype=float)
    arr_te = np.asarray(catalog.load(f"{prefix}_test"),  dtype=float)
    if arr_tr.ndim == 1: arr_tr = arr_tr[:, None]
    if arr_te.ndim == 1: arr_te = arr_te[:, None]
    X_tr_parts.append(arr_tr)
    X_te_parts.append(arr_te)

X_tr_comb = np.hstack(X_tr_parts)
X_te_comb = np.hstack(X_te_parts)

# 4) Classifier pool
classifiers = {
    # "LogisticRegression":   LogisticRegression(max_iter=500),
    # "RandomForest":         RandomForestClassifier(n_estimators=100, random_state=42),
    # "GradientBoosting":     GradientBoostingClassifier(n_estimators=100, random_state=42),
    # "SVM (RBF kernel)":     SVC(kernel='rbf', probability=True, random_state=42),
    "K-Nearest Neighbors":  KNeighborsClassifier(n_neighbors=5),
}

def weighted_f1(clf, X_tr, y_tr, X_te, y_te):
    clf.fit(X_tr, y_tr)
    return f1_score(y_te, clf.predict(X_te), average="weighted")

# 5) Evaluate on the **combined** embedding
print("=== COMBINED EMBEDDING ===")

print("  BINARY (low vs high vol):")
for name, clf in classifiers.items():
    score = weighted_f1(clf, X_tr_comb, y_binary_train, X_te_comb, y_binary_test)
    print(f"    {name:25s} → wF1 = {score:.4f}")

print("\n  MULTI-CLASS (low/med/high):")
for name, clf in classifiers.items():
    if name == "LogisticRegression":
        clf = LogisticRegression(multi_class="multinomial", solver="lbfgs", max_iter=500)
    score = weighted_f1(clf, X_tr_comb, y_multi_train, X_te_comb, y_multi_test)
    print(f"    {name:25s} → wF1 = {score:.4f}")


[05/28/25 20:50:15] INFO     Loading data from train_prices (ParquetDataset)...                 ]8;id=105424;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=850702;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from test_prices (ParquetDataset)...                  ]8;id=956046;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=453450;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

[05/28/25 20:50:16] INFO     Loading data from autoencoder_train (ParquetDataset)...            ]8;id=667674;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=659491;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from autoencoder_test (ParquetDataset)...             ]8;id=582972;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=436741;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from fft_train (ParquetDataset)...                    ]8;id=785263;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=902465;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

...

                    INFO     Loading data from wavelet_train (ParquetDataset)...                ]8;id=331016;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=139860;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from wavelet_test (ParquetDataset)...                 ]8;id=220446;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=443978;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

=== COMBINED EMBEDDING ===
  BINARY (low vs high vol):


[05/28/25 20:50:23] WARNING  /Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/l ]8;id=733972;file:///Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/warnings.py\warnings.py]8;;\:]8;id=737349;file:///Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/warnings.py#109\109]8;;\
                             ib/python3.11/site-packages/threadpoolctl.py:1226: RuntimeWarning:                    
                             Found Intel OpenMP ('libiomp') and LLVM OpenMP ('libomp') loaded at                   
                             the same time. Both libraries are known to be incompatible and this                   
                             can cause random crashes or deadlocks on Linux when loaded in the                     
                             same Python program.                                                                  
                             Using threadpoolctl may cause crashes or deadlocks. For more                          
                             information and possible workarounds, please see                                      
                                 https://github.com/joblib/threadpoolctl/blob/master/multiple_openm                
                             p.md                                                                                  
                                                                                                                   
                               warnings.warn(msg, RuntimeWarning)                                                  
                                                                                                                   

    K-Nearest Neighbors       → wF1 = 0.5321

  MULTI-CLASS (low/med/high):
    K-Nearest Neighbors       → wF1 = 0.4019


In [7]:
import numpy as np

# correct imports
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import f1_score

def create_raw_windows(series, window_size):
    arr = np.asarray(series, dtype=float)
    return [arr[i:i+window_size] for i in range(len(arr) - window_size + 1)]

def realized_volatility(windows):
    return np.array([np.std(np.diff(np.log(w))) for w in windows])

# — PARAMETERS —
window_size = 90
skip_images = {"gaf", "mtf", "rp"}

# *** HERE: pick which embeddings to combine ***
# Leave as [] (or None) to use *all* available non-image embeddings:
selected_prefixes = ["pca", "autoencoder", "wavelet"]  # e.g. only PCA, UMAP & Wavelet
# selected_prefixes = []  # <-- uncomment to combine *all* automatically discovered ones

# 1) Load price series & build vol‐based labels
train_df = catalog.load("train_prices")
test_df  = catalog.load("test_prices")
price_train = train_df["price_close"].values.astype(float)
price_test  = test_df["price_close"].values.astype(float)

wins_tr = create_raw_windows(price_train, window_size)
wins_te = create_raw_windows(price_test,  window_size)
vols_tr = realized_volatility(wins_tr)
vols_te = realized_volatility(wins_te)

# binary labels
thresh_25       = np.percentile(vols_tr, 75)
y_binary_train  = (vols_tr >= thresh_25).astype(int)
y_binary_test   = (vols_te >=  thresh_25).astype(int)

# multi-class labels
low_thr, high_thr   = np.percentile(vols_tr, [33, 66])
y_multi_train       = np.digitize(vols_tr, bins=[low_thr, high_thr], right=True)
y_multi_test        = np.digitize(vols_te, bins=[low_thr, high_thr], right=True)

# 2) Discover all non-image embeddings
all_ds    = catalog.list()
train_ds  = [n for n in all_ds if n.endswith("_train")]
all_pref  = sorted({
    ds.rsplit("_",1)[0] for ds in train_ds
    if not ds.startswith(f"windows_{window_size}") and ds.rsplit("_",1)[0] not in skip_images
})

# if user didn't pick any, combine all
if not selected_prefixes:
    prefixes = all_pref
else:
    prefixes = [p for p in selected_prefixes if p in all_pref]
    missing = set(selected_prefixes) - set(prefixes)
    if missing:
        raise ValueError(f"These embeddings not found: {missing}")

print(">>> combining embeddings:", prefixes)

# 3) Load & concatenate
X_tr_parts = []
X_te_parts = []
for prefix in prefixes:
    arr_tr = np.asarray(catalog.load(f"{prefix}_train"), dtype=float)
    arr_te = np.asarray(catalog.load(f"{prefix}_test"),  dtype=float)
    if arr_tr.ndim == 1: arr_tr = arr_tr[:, None]
    if arr_te.ndim == 1: arr_te = arr_te[:, None]
    X_tr_parts.append(arr_tr)
    X_te_parts.append(arr_te)

X_tr_comb = np.hstack(X_tr_parts)
X_te_comb = np.hstack(X_te_parts)

# 4) Classifier pool
classifiers = {
    "LogisticRegression":   LogisticRegression(max_iter=500),
    "RandomForest":         RandomForestClassifier(n_estimators=100, random_state=42),
    "GradientBoosting":     GradientBoostingClassifier(n_estimators=100, random_state=42),
    "SVM (RBF kernel)":     SVC(kernel='rbf', probability=True, random_state=42),
    "K-Nearest Neighbors":  KNeighborsClassifier(n_neighbors=5),
}

def weighted_f1(clf, X_tr, y_tr, X_te, y_te):
    clf.fit(X_tr, y_tr)
    return f1_score(y_te, clf.predict(X_te), average="weighted")

# 5) Evaluate on the **combined** embedding
print("\n=== COMBINED EMBEDDING ===")

print("  BINARY (low vs high vol):")
for name, clf in classifiers.items():
    score = weighted_f1(clf, X_tr_comb, y_binary_train, X_te_comb, y_binary_test)
    print(f"    {name:25s} → wF1 = {score:.4f}")

print("\n  MULTI-CLASS (low/med/high):")
for name, clf in classifiers.items():
    if name == "LogisticRegression":
        clf = LogisticRegression(multi_class="multinomial", solver="lbfgs", max_iter=500)
    score = weighted_f1(clf, X_tr_comb, y_multi_train, X_te_comb, y_multi_test)
    print(f"    {name:25s} → wF1 = {score:.4f}")


[05/28/25 20:52:01] INFO     Loading data from train_prices (ParquetDataset)...                 ]8;id=979328;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=347593;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from test_prices (ParquetDataset)...                  ]8;id=91394;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=892212;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

>>> combining embeddings: ['pca', 'autoencoder', 'wavelet']


[05/28/25 20:52:02] INFO     Loading data from pca_train (ParquetDataset)...                    ]8;id=864798;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=81018;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from pca_test (ParquetDataset)...                     ]8;id=891734;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=664187;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

...


=== COMBINED EMBEDDING ===
  BINARY (low vs high vol):
    LogisticRegression        → wF1 = 0.4564
    RandomForest              → wF1 = 0.4889
    GradientBoosting          → wF1 = 0.4756
    SVM (RBF kernel)          → wF1 = 0.4870
    K-Nearest Neighbors       → wF1 = 0.6407

  MULTI-CLASS (low/med/high):


[05/28/25 20:55:32] WARNING  /Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/l ]8;id=148431;file:///Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/warnings.py\warnings.py]8;;\:]8;id=600078;file:///Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/warnings.py#109\109]8;;\
                             ib/python3.11/site-packages/sklearn/linear_model/_logistic.py:1247:                   
                             FutureWarning: 'multi_class' was deprecated in version 1.5 and will be                
                             removed in 1.7. From then on, it will always use 'multinomial'. Leave                 
                             it to its default value to avoid this warning.                                        
                               warnings.warn(                                                                      
                                                                                                                   

[05/28/25 20:55:34] WARNING  /Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/l ]8;id=923842;file:///Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/warnings.py\warnings.py]8;;\:]8;id=764606;file:///Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/warnings.py#109\109]8;;\
                             ib/python3.11/site-packages/sklearn/linear_model/_logistic.py:465:                    
                             ConvergenceWarning: lbfgs failed to converge (status=1):                              
                             STOP: TOTAL NO. OF ITERATIONS REACHED LIMIT.                                          
                                                                                                                   
                             Increase the number of iterations (max_iter) or scale the data as                     
                             shown in:                                                                             
                                 https://scikit-learn.org/stable/modules/preprocessing.html                        
                             Please also refer to the documentation for alternative solver options:                
                                 https://scikit-learn.org/stable/modules/linear_model.html#logistic                
                             -regression                                                                           
                               n_iter_i = _check_optimize_result(                                                  
                                                                                                                   

    LogisticRegression        → wF1 = 0.3705
    RandomForest              → wF1 = 0.4359


╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <module>:105                                                                                  │
│                                                                                                  │
│   102 for name, clf in classifiers.items():                                                      │
│   103 │   if name == "LogisticRegression":                                                       │
│   104 │   │   clf = LogisticRegression(multi_class="multinomial", solver="lbfgs", max_iter=500   │
│ ❱ 105 │   score = weighted_f1(clf, X_tr_comb, y_multi_train, X_te_comb, y_multi_test)            │
│   106 │   print(f"    {name:25s} → wF1 = {score:.4f}")                                           │
│   107                                                                                            │
│                                                                                                  │
│ in weighted_f1:90                                                                                │
│                                                                                                  │
│    87 }                                                                                          │
│    88                                                                                            │
│    89 def weighted_f1(clf, X_tr, y_tr, X_te, y_te):                                              │
│ ❱  90 │   clf.fit(X_tr, y_tr)                                                                    │
│    91 │   return f1_score(y_te, clf.predict(X_te), average="weighted")                           │
│    92                                                                                            │
│    93 # 5) Evaluate on the **combined** embedding                                                │
│                                                                                                  │
│ /Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-package │
│ s/sklearn/base.py:1389 in wrapper                                                                │
│                                                                                                  │
│   1386 │   │   │   │   │   prefer_skip_nested_validation or global_skip_validation               │
│   1387 │   │   │   │   )                                                                         │
│   1388 │   │   │   ):                                                                            │
│ ❱ 1389 │   │   │   │   return fit_method(estimator, *args, **kwargs)                             │
│   1390 │   │                                                                                     │
│   1391 │   │   return wrapper                                                                    │
│   1392                                                                                           │
│                                                                                                  │
│ /Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-package │
│ s/sklearn/ensemble/_gb.py:787 in fit                                                             │
│                                                                                                  │
│    784 │   │   │   self._resize_state()                                                          │
│    785 │   │                                                                                     │
│    786 │   │   # fit the boosting stages                                                         │
│ ❱  787 │   │   n_stages = self._fit_stages(                                                      │
│    788 │   │   │   X_train,                                                                      │
│    789 │   │   │   y_train,                                

In [10]:
import numpy as np
import itertools

from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import f1_score

# 1) helper functions
def create_raw_windows(series, window_size):
    arr = np.asarray(series, dtype=float)
    return [arr[i:i+window_size] for i in range(len(arr) - window_size + 1)]

def realized_volatility(windows):
    return np.array([np.std(np.diff(np.log(w))) for w in windows])

def weighted_f1(clf, X_tr, y_tr, X_te, y_te):
    clf.fit(X_tr, y_tr)
    return f1_score(y_te, clf.predict(X_te), average="weighted")


# — PARAMETERS —
window_size   = 90
skip_images   = {"gaf", "mtf", "rp"}

# 2) build your vol-based labels
train_df      = catalog.load("train_prices")
test_df       = catalog.load("test_prices")
price_tr      = train_df["price_close"].astype(float).values
price_te      = test_df ["price_close"].astype(float).values

wins_tr       = create_raw_windows(price_tr, window_size)
wins_te       = create_raw_windows(price_te, window_size)
vols_tr       = realized_volatility(wins_tr)
vols_te       = realized_volatility(wins_te)

# 2a) binary: top 25% vs rest
thr25         = np.percentile(vols_tr, 75)
y_bin_tr      = (vols_tr >= thr25).astype(int)
y_bin_te      = (vols_te >= thr25).astype(int)

# 2b) multi: low/med/high via 33/66
low33, high66 = np.percentile(vols_tr, [33, 66])
y_mul_tr      = np.digitize(vols_tr, bins=[low33, high66], right=True)
y_mul_te      = np.digitize(vols_te, bins=[low33, high66], right=True)


# 3) discover your embedding prefixes
all_ds   = catalog.list()
train_ds = [n for n in all_ds if n.endswith("_train")]
prefixes = sorted({
    ds.rsplit("_",1)[0]
    for ds in train_ds
    if not ds.startswith(f"windows_{window_size}") 
       and ds.rsplit("_",1)[0] not in skip_images
})


# 4) prepare classifier constructors
clf_constructors = {
    # "LogisticRegression":   lambda multiclass=False: LogisticRegression(
    #                             **({"multi_class":"multinomial","solver":"lbfgs"} if multiclass else {}),
    #                             max_iter=500
    #                          ),
    # "RandomForest":         lambda multiclass=False: RandomForestClassifier(n_estimators=100, random_state=42),
    # "GradientBoosting":     lambda multiclass=False: GradientBoostingClassifier(n_estimators=100, random_state=42),
    # "SVM (RBF kernel)":     lambda multiclass=False: SVC(kernel='rbf', probability=True, random_state=42),
    "K-Nearest Neighbors":  lambda multiclass=False: KNeighborsClassifier(n_neighbors=5),
}


# 5) loop over all 2-element combinations & evaluate
results_bin = []
results_mul = []

for combo in itertools.combinations(prefixes, 3):
    # load + concat embeddings for this pair
    parts_tr = []
    parts_te = []
    for p in combo:
        arr_tr = np.asarray(catalog.load(f"{p}_train"), dtype=float)
        arr_te = np.asarray(catalog.load(f"{p}_test"),  dtype=float)
        if arr_tr.ndim == 1: arr_tr = arr_tr[:,None]
        if arr_te.ndim == 1: arr_te = arr_te[:,None]
        parts_tr.append(arr_tr)
        parts_te.append(arr_te)
    X_tr = np.hstack(parts_tr)
    X_te = np.hstack(parts_te)
    
    # binary task
    f1s = []
    for name, make_clf in clf_constructors.items():
        f1s.append(weighted_f1(make_clf(False), X_tr, y_bin_tr, X_te, y_bin_te))
    results_bin.append((combo, np.mean(f1s)))
    
    # multi-class task
    f1s = []
    for name, make_clf in clf_constructors.items():
        f1s.append(weighted_f1(make_clf(True), X_tr, y_mul_tr, X_te, y_mul_te))
    results_mul.append((combo, np.mean(f1s)))


# 6) sort & print top combos
results_bin.sort(key=lambda x: x[1], reverse=True)
results_mul.sort(key=lambda x: x[1], reverse=True)

print("\nTop 10 embedding-pairs for BINARY task (avg wF1):")
for combo, score in results_bin[:10]:
    print(f"  {combo[0]:<8} + {combo[1]:<8} → {score:.4f}")

print("\nTop 10 embedding-pairs for MULTI-CLASS task (avg wF1):")
for combo, score in results_mul[:10]:
    print(f"  {combo[0]:<8} + {combo[1]:<8} → {score:.4f}")


[05/28/25 21:11:19] INFO     Loading data from train_prices (ParquetDataset)...                 ]8;id=733003;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=716357;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from test_prices (ParquetDataset)...                  ]8;id=539170;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=19777;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from autoencoder_train (ParquetDataset)...            ]8;id=165677;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=946266;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from autoencoder_test (ParquetDataset)...             ]8;id=852571;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=606882;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from fft_train (ParquetDataset)...                    ]8;id=50741;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=184810;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

...

                    INFO     Loading data from umap_train (ParquetDataset)...                   ]8;id=271364;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=92747;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from umap_test (ParquetDataset)...                    ]8;id=545304;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=31380;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from wavelet_train (ParquetDataset)...                ]8;id=108747;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=181991;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from wavelet_test (ParquetDataset)...                 ]8;id=624301;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=604666;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\


Top 10 embedding-pairs for BINARY task (avg wF1):
  lle      + rp_clip  → 0.6730
  autoencoder + pca      → 0.6708
  lle      + pca      → 0.6693
  pca      + rp_clip  → 0.6664
  autoencoder + gaf_clip → 0.6627
  autoencoder + rp_clip  → 0.6618
  gaf_clip + rp_clip  → 0.6608
  gaf_clip + lle      → 0.6576
  gaf_clip + pca      → 0.6559
  mtf_clip + rp_clip  → 0.6558

Top 10 embedding-pairs for MULTI-CLASS task (avg wF1):
  autoencoder + graph    → 0.4646
  gaf_resnet + lle      → 0.4577
  autoencoder + lle      → 0.4526
  gaf_clip + gaf_dino → 0.4506
  gaf_resnet + mtf_clip → 0.4506
  graph    + rp_clip  → 0.4505
  autoencoder + graph    → 0.4503
  graph    + lle      → 0.4494
  gaf_clip + gaf_resnet → 0.4491
  graph    + mtf_resnet → 0.4465


In [19]:
import numpy as np
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import f1_score

# 1) helper functions
def create_raw_windows(series, window_size):
    arr = np.asarray(series, dtype=float)
    return [arr[i:i+window_size] for i in range(len(arr) - window_size + 1)]

def realized_volatility(windows):
    return np.array([np.std(np.diff(np.log(w))) for w in windows])

def weighted_f1(clf, X_tr, y_tr, X_te, y_te):
    clf.fit(X_tr, y_tr)
    return f1_score(y_te, clf.predict(X_te), average="weighted")


# — PARAMETERS —
window_size = 90
skip_images = {"gaf", "mtf", "rp"}

# 2) build your vol-based labels
train_df = catalog.load("train_prices")
test_df  = catalog.load("test_prices")
price_tr = train_df["price_close"].astype(float).values
price_te = test_df ["price_close"].astype(float).values

wins_tr = create_raw_windows(price_tr, window_size)
wins_te = create_raw_windows(price_te, window_size)
vols_tr = realized_volatility(wins_tr)
vols_te = realized_volatility(wins_te)

# 2a) binary: top 25% vs rest
thr25    = np.percentile(vols_tr, 75)
y_bin_tr = (vols_tr >= thr25).astype(int)
y_bin_te = (vols_te >= thr25).astype(int)

# 2b) multi: low/med/high via 33/66
low33, high66 = np.percentile(vols_tr, [33, 66])
y_mul_tr      = np.digitize(vols_tr, bins=[low33, high66], right=True)
y_mul_te      = np.digitize(vols_te, bins=[low33, high66], right=True)


# 3) discover your embedding prefixes
all_ds   = catalog.list()
train_ds = [n for n in all_ds if n.endswith("_train")]
prefixes = sorted({
    ds.rsplit("_",1)[0]
    for ds in train_ds
    if not ds.startswith(f"windows_{window_size}") 
       and ds.rsplit("_",1)[0] not in skip_images
})


# 4) prepare classifier constructors
clf_constructors = {
    "K-Nearest Neighbors": lambda multiclass=False: KNeighborsClassifier(n_neighbors=5),
}


# 5) loop over single embeddings & evaluate
results_bin = []
results_mul = []

for p in prefixes:
    # load embeddings for this prefix
    arr_tr = np.asarray(catalog.load(f"{p}_train"), dtype=float)
    arr_te = np.asarray(catalog.load(f"{p}_test"),  dtype=float)
    if arr_tr.ndim == 1: arr_tr = arr_tr[:, None]
    if arr_te.ndim == 1: arr_te = arr_te[:, None]
    X_tr, X_te = arr_tr, arr_te

    # binary task
    f1s = [weighted_f1(make_clf(False), X_tr, y_bin_tr, X_te, y_bin_te)
           for _, make_clf in clf_constructors.items()]
    results_bin.append((p, np.mean(f1s)))

    # multi-class task
    f1s = [weighted_f1(make_clf(True), X_tr, y_mul_tr, X_te, y_mul_te)
           for _, make_clf in clf_constructors.items()]
    results_mul.append((p, np.mean(f1s)))


# 6) sort & print top embeddings
results_bin.sort(key=lambda x: x[1], reverse=True)
results_mul.sort(key=lambda x: x[1], reverse=True)

print("\nTop 10 single embeddings for BINARY task (avg wF1):")
for prefix, score in results_bin[:10]:
    print(f"  {prefix:<15} → {score:.4f}")

print("\nTop 10 single embeddings for MULTI-CLASS task (avg wF1):")
for prefix, score in results_mul[:10]:
    print(f"  {prefix:<15} → {score:.4f}")


[05/29/25 23:12:50] INFO     Loading data from train_prices (ParquetDataset)...                 ]8;id=880539;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=299716;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from test_prices (ParquetDataset)...                  ]8;id=453919;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=62440;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

[05/29/25 23:12:51] INFO     Loading data from autoencoder_train (ParquetDataset)...            ]8;id=173341;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=4791;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from autoencoder_test (ParquetDataset)...             ]8;id=404333;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=493463;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

[05/29/25 23:12:52] INFO     Loading data from fft_train (ParquetDataset)...                    ]8;id=782913;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=242614;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

...

                    INFO     Loading data from umap_train (ParquetDataset)...                   ]8;id=959907;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=5182;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from umap_test (ParquetDataset)...                    ]8;id=422952;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=219414;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

[05/29/25 23:13:11] INFO     Loading data from wavelet_train (ParquetDataset)...                ]8;id=262431;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=539579;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

                    INFO     Loading data from wavelet_test (ParquetDataset)...                 ]8;id=302611;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=230378;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\


Top 10 single embeddings for BINARY task (avg wF1):
  wavelet         → 0.6437
  pca             → 0.6301
  autoencoder     → 0.6245
  lle             → 0.5848
  gaf_clip        → 0.5712
  umap            → 0.5645
  gaf_resnet      → 0.5562
  rp_resnet       → 0.5372
  mtf_dino        → 0.5359
  gaf_dino        → 0.5287

Top 10 single embeddings for MULTI-CLASS task (avg wF1):
  autoencoder     → 0.4426
  pca             → 0.4347
  gaf_dino        → 0.4180
  gaf_resnet      → 0.4123
  gaf_clip        → 0.4103
  lle             → 0.4099
  rp_clip         → 0.4088
  graph           → 0.4028
  wavelet         → 0.3927
  tda             → 0.3879


In [14]:
print("\nTop 10 embedding-pairs for BINARY task (avg wF1):")
for combo, score in results_bin[:10]:
    print(f"  {combo[0]:<8} + {combo[1]:<8} + {combo[2]:<8}→ {score:.4f}")

print("\nTop 10 embedding-pairs for MULTI-CLASS task (avg wF1):")
for combo, score in results_mul[:10]:
    print(f"  {combo[0]:<8} + {combo[1]:<8} + {combo[2]:<8}→ {score:.4f}")


Top 10 embedding-pairs for BINARY task (avg wF1):
  lle      + rp_clip  + wavelet → 0.6730
  autoencoder + pca      + rp_clip → 0.6708
  lle      + pca      + rp_clip → 0.6693
  pca      + rp_clip  + wavelet → 0.6664
  autoencoder + gaf_clip + wavelet → 0.6627
  autoencoder + rp_clip  + wavelet → 0.6618
  gaf_clip + rp_clip  + wavelet → 0.6608
  gaf_clip + lle      + wavelet → 0.6576
  gaf_clip + pca      + wavelet → 0.6559
  mtf_clip + rp_clip  + wavelet → 0.6558

Top 10 embedding-pairs for MULTI-CLASS task (avg wF1):
  autoencoder + graph    + umap    → 0.4646
  gaf_resnet + lle      + rp_clip → 0.4577
  autoencoder + lle      + rp_clip → 0.4526
  gaf_clip + gaf_dino + gaf_resnet→ 0.4506
  gaf_resnet + mtf_clip + rp_clip → 0.4506
  graph    + rp_clip  + umap    → 0.4505
  autoencoder + graph    + lle     → 0.4503
  graph    + lle      + umap    → 0.4494
  gaf_clip + gaf_resnet + rp_clip → 0.4491
  graph    + mtf_resnet + rp_clip → 0.4465


In [17]:
catalog.load("umap_train")

[05/29/25 22:31:17] INFO     Loading data from umap_train (ParquetDataset)...                   ]8;id=999103;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=84211;file:///Users/RoverHofman/Desktop/School/thesis/embedding-forecasting/.venv/lib/python3.11/site-packages/kedro/io/data_catalog.py#401\401]8;;\

UMAP1     UMAP2
0     -1.878755  4.162723
1     -1.902186  4.180915
2     -1.947510  4.241618
3     -1.902471  4.178031
4     -1.916329  4.282709
...         ...       ...
15138  5.027134  2.349466
15139  5.085326  2.569490
15140  5.198251  2.759428
15141  5.233144  2.897991
15142  5.221097  3.085845

[15143 rows x 2 columns]